In [5]:
# imports

import os
import requests
from IPython.display import Markdown, display, update_display
from huggingface_hub import login
from transformers import AutoTokenizer, AutoModelForCausalLM, TextStreamer, BitsAndBytesConfig, AutoModelForSpeechSeq2Seq, AutoProcessor, pipeline
import torch

In [4]:
# Quantization Config is a proccess allows us to load the model into memory and use less memory by lowering the value of the weights from their
# initial type of 32 bit float values to 8 or even 4 bits. This dramatically increases the loading of the model and calculations without 
# having an extreme depreciation of the final result

# will not be using it because of my amd not being able to run cuda
#quant_config = BitsAndBytesConfig(
#    load_in_4bit=True,
#    bnb_4bit_use_double_quant=True,
#    bnb_4bit_compute_dtype=torch.bfloat16,
#    bnb_4bit_quant_type="nf4"
#)

In [27]:
LLAMA = "meta-llama/Llama-3.2-1B-Instruct"
PHI35 = "microsoft/Phi-3.5-mini-instruct"
WHISPER = "openai/whisper-large-v3-turbo"
TALK= "suno/bark-small"

In [20]:
# general function for calling a model using the model approach and not pipelines
def generate(model, messages):
  tokenizer = AutoTokenizer.from_pretrained(model)
  tokenizer.pad_token = tokenizer.eos_token
  inputs = tokenizer.apply_chat_template(messages, return_tensors="pt", add_generation_prompt=True)#.to("cuda")
  streamer = TextStreamer(tokenizer)
  model = AutoModelForCausalLM.from_pretrained(model, device_map="auto")#, quantization_config=quant_config)
  outputs = model.generate(inputs, max_new_tokens=80, streamer=streamer)
  del tokenizer, streamer, model, inputs, outputs
  torch.cuda.empty_cache()

In [25]:
# I will first create a random meeting mp3 using a text to speech model
meeting_text = """
Good morning, everyone. Thanks for joining the meeting today. Let’s dive right into the agenda. 

First, I’d like to discuss the progress on the marketing campaign we’ve been working on. Alex, can you give us a quick update on the latest numbers?

[Pause for response]

Great to hear that the engagement is up by 20%. That’s fantastic news. Moving on to the next item: the upcoming product launch. Sam, what’s the latest on the production timeline?

[Pause for response]

Okay, so we’re looking at a delay of about two weeks. That’s something we need to communicate to the stakeholders ASAP. Jordan, can you draft an email to keep everyone in the loop?

[Pause for response]

Perfect. Let’s also discuss the budget for the next quarter. We need to allocate more resources to the R&D team to meet their requests. Does anyone have any concerns or suggestions about the proposed budget?

[Pause for response]

Alright, it sounds like we’re all on the same page. Let’s finalize the budget by the end of the week. Finally, are there any other items anyone would like to add to the agenda before we wrap up?

[Pause for response]

No? Great. Let’s adjourn the meeting here. Thanks, everyone, for your time and contributions. Let’s keep up the good work!
"""

In [40]:
dataset = load_dataset("distil-whisper/librispeech_long", "clean", split="validation")
sample = dataset[0]["audio"]

README.md:   0%|          | 0.00/480 [00:00<?, ?B/s]

C:\Users\Darks\anaconda3\envs\llms\Lib\site-packages\huggingface_hub\file_download.py:140: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\Darks\.cache\huggingface\hub\datasets--distil-whisper--librispeech_long. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)


(…)-00000-of-00001-913508124a40cb97.parquet:   0%|          | 0.00/1.98M [00:00<?, ?B/s]

Generating validation split:   0%|          | 0/1 [00:00<?, ? examples/s]

ImportError: To support decoding audio files, please install 'librosa' and 'soundfile'.

In [34]:
from IPython.display import Audio

Audio(output_meeting, rate=modelSpeech.config.sampling_rate)

dict

In [10]:
from datasets import load_dataset
import gradio as gr

device = "cuda:0" if torch.cuda.is_available() else "cpu"
torch_dtype = torch.float16 if torch.cuda.is_available() else torch.float32

model = AutoModelForSpeechSeq2Seq.from_pretrained(
    WHISPER, torch_dtype=torch_dtype, low_cpu_mem_usage=True
)
model.to(device)

processor = AutoProcessor.from_pretrained(WHISPER)

pipe = pipeline(
    "automatic-speech-recognition",
    model=model,
    tokenizer=processor.tokenizer,
    feature_extractor=processor.feature_extractor,
    chunk_length_s=30,
    batch_size=16,  # batch size for inference - set based on your device
    torch_dtype=torch_dtype,
    device=device,
)


Device set to use cpu


In [ ]:
def transcribe_audio(audio_file):
    # Process the uploaded audio file
    result = pipe(audio_file)
    return result["text"]

In [11]:
# Create Gradio interface
with gr.Blocks() as demo:
    gr.Markdown("# Audio to Text Transcription")
    
    with gr.Row():
        audio_input = gr.Audio(label="Upload an audio file")
        button = gr.Button("Transcribe")
    
    text_output = gr.Textbox(label="Transcribed text")

    button.click(
        fn=transcribe_audio,
        inputs=audio_input,
        outputs=text_output
    )

demo.launch()

* Running on local URL:  http://127.0.0.1:7861

To create a public link, set `share=True` in `launch()`.
